In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error


In [2]:
data = pd.read_csv('/Users/yagmurozdemir/Desktop/MCP_PREDICTIONS.csv')

data.fillna(method='ffill', inplace=True)

cols = ['Workday', 'Workday_24', 'Workday_168']
data[cols] = data[cols].astype(int)


In [3]:
data

DateTime  renewable_ratio  priceEur  Difference_24  \
0      2021-01-14T00:00:00Z         0.040737     35.26           1.16   
1      2021-01-14T01:00:00Z         0.045864     35.13           4.79   
2      2021-01-14T02:00:00Z         0.051034     34.87           2.32   
3      2021-01-14T03:00:00Z         0.059953     34.58           7.66   
4      2021-01-14T04:00:00Z         0.062077     34.57           6.45   
...                     ...              ...       ...            ...   
28747  2024-04-25T19:00:00Z         0.106919     77.99           0.00   
28748  2024-04-25T20:00:00Z         0.101651     77.99           0.00   
28749  2024-04-25T21:00:00Z         0.102125     77.99           0.00   
28750  2024-04-25T22:00:00Z         0.096134     77.99           0.00   
28751  2024-04-25T23:00:00Z         0.098048     77.99           0.00   

       Difference_168  Workday  Workday_168  Workday_24  forecast  \
0                2.17        1            1           1     27.40   
1                0.94        1            1           1     30.10   
2                5.17        1            1           1     37.30   
3                5.35        1            1           1     41.00   
4                7.32        1            1           1     52.60   
...               ...      ...          ...         ...       ...   
28747           -0.44        1            1           1    264.01   
28748           -0.44        1            1           1    219.62   
28749           -0.44        1            1           1    191.99   
28750            1.04        1            1           1    157.67   
28751           10.57        1            1           1    134.85   

       BV Forecast  price_lag_24  price_lag_168  forecasted_price_eur  
0          4187.97         34.10          33.09             46.060030  
1          3975.82         30.34          34.19             44.125388  
2          3885.02         32.55          29.70             42.345044  
3          3589.79         26.92          29.23             38.267237  
4          3137.07         28.12          27.25             37.610058  
...            ...           ...            ...                   ...  
28747      4703.63         77.99          78.43             80.214039  
28748      4501.67         77.99          78.43             80.901090  
28749      4394.75         77.99          78.43             80.839259  
28750      4235.98         77.99          76.95             80.908118  
28751      4053.30         77.99          67.42             76.070862  

[28752 rows x 13 columns]

In [6]:
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.neighbors import NearestNeighbors

data['DateTime'] = pd.to_datetime(data['DateTime'], errors='coerce', utc=True)
data['Hour'] = data['DateTime'].dt.hour

train_start = pd.to_datetime('2021-01-01', utc=True)
test_start = pd.to_datetime('2023-04-25', utc=True)
test_end = pd.to_datetime('2024-04-26', utc=True)

features = ['renewable_ratio', 'Difference_24', 'Difference_168', 'Workday', 'Workday_168', 'Workday_24', 'forecast', 'BV Forecast', 'price_lag_24', 'price_lag_168']

test_datetimes = []
prediction_datetimes = []

for hour in range(24):
    test_data_hour = data[(data['DateTime'] >= test_start) & (data['DateTime'] <= test_end) & (data['Hour'] == hour)]
    
    for test_date in pd.date_range(test_start, test_end, freq='D'):
        train_end = test_date - pd.Timedelta(days=1)
        train_data_hour = data[(data['DateTime'] >= train_start) & (data['DateTime'] <= train_end) & (data['Hour'] == hour)]
        
        if not train_data_hour.empty and not test_data_hour.empty:
            scaler = StandardScaler()
            train_data_scaled = train_data_hour.copy()
            train_data_scaled[features] = scaler.fit_transform(train_data_scaled[features])
            test_data_scaled = test_data_hour.copy()
            test_data_scaled[features] = scaler.transform(test_data_scaled[features])

            knn = NearestNeighbors(n_neighbors=3)
            knn.fit(train_data_scaled[features])

            distances, indices = knn.kneighbors(test_data_scaled[features])

            for i, test_datetime in enumerate(test_data_scaled['DateTime'].values):
                test_datetimes.extend([test_datetime] * 3)
                prediction_datetimes.extend(train_data_hour.iloc[indices[i]]['DateTime'].values)

assert len(test_datetimes) == len(prediction_datetimes), "Lengths of test_datetimes and prediction_datetimes do not match"

hourly_results = pd.DataFrame({
    'Test DateTime': test_datetimes,
    'Prediction DateTime': prediction_datetimes
})

hourly_results['Test DateTime'] = pd.to_datetime(hourly_results['Test DateTime'], utc=True)
hourly_results['Prediction DateTime'] = pd.to_datetime(hourly_results['Prediction DateTime'], utc=True)

hourly_results['Test Date'] = hourly_results['Test DateTime'].dt.date
daily_results = {}

for day in pd.date_range(test_start, test_end - pd.Timedelta(days=1), freq='D'):
    day_start = day
    day_end = day + pd.Timedelta(hours=23)

    day_data = hourly_results[(hourly_results['Test DateTime'] >= day_start) & (hourly_results['Test DateTime'] <= day_end)]

    day_prediction_dates = pd.to_datetime(day_data['Prediction DateTime']).dt.date.values

    if len(day_prediction_dates) > 0:
        most_frequent_date = pd.Series(day_prediction_dates - pd.Timedelta(days=1)).mode().iloc[0]
        daily_results[day.date()] = most_frequent_date

daily_results_df = pd.DataFrame(list(daily_results.items()), columns=['Test Date', 'Prediction Date'])

print(daily_results_df)


      Test Date Prediction Date
0    2023-04-25      2023-04-24
1    2023-04-26      2023-04-25
2    2023-04-27      2023-04-26
3    2023-04-28      2023-04-27
4    2023-04-29      2023-04-28
..          ...             ...
362  2024-04-21      2021-04-07
363  2024-04-22      2023-11-05
364  2024-04-23      2021-07-14
365  2024-04-24      2021-07-23
366  2024-04-25      2021-12-06

[367 rows x 2 columns]


## date selection

In [7]:
daily_results_df

Test Date Prediction Date
0    2023-04-25      2023-04-24
1    2023-04-26      2023-04-25
2    2023-04-27      2023-04-26
3    2023-04-28      2023-04-27
4    2023-04-29      2023-04-28
..          ...             ...
362  2024-04-21      2021-04-07
363  2024-04-22      2023-11-05
364  2024-04-23      2021-07-14
365  2024-04-24      2021-07-23
366  2024-04-25      2021-12-06

[367 rows x 2 columns]

In [9]:
daily_results_df.to_csv('daily_results_df.csv', index=False)


In [12]:
hours = list(range(24))

test_dates_expanded = daily_results_df['Test Date'].repeat(24).reset_index(drop=True)

prediction_dates_expanded = daily_results_df['Prediction Date'].repeat(24).reset_index(drop=True)

expanded_df = pd.DataFrame({
    'Test Date': test_dates_expanded,
    'Hour': hours * len(daily_results_df),
    'Prediction Date': prediction_dates_expanded
})

print(expanded_df)

       Test Date  Hour Prediction Date
0     2023-04-25     0      2022-01-30
1     2023-04-25     1      2022-01-30
2     2023-04-25     2      2022-01-30
3     2023-04-25     3      2022-01-30
4     2023-04-25     4      2022-01-30
...          ...   ...             ...
8803  2024-04-25    19      2023-03-12
8804  2024-04-25    20      2023-03-12
8805  2024-04-25    21      2023-03-12
8806  2024-04-25    22      2023-03-12
8807  2024-04-25    23      2023-03-12

[8808 rows x 3 columns]


In [13]:
data_df = data.copy()

In [14]:
data_df['DateTime'] = pd.to_datetime(data_df['DateTime'])
data_df['date'] = data_df['DateTime'].dt.strftime('%Y-%m-%d')
data_df['hour'] = data_df['DateTime'].dt.hour


In [15]:
expanded_df['Prediction Date'] = pd.to_datetime(expanded_df['Prediction Date']).dt.strftime('%Y-%m-%d')

merged_df = expanded_df.merge(data_df, left_on=['Prediction Date', 'Hour'], right_on=['date', 'hour'], how='left')


In [16]:
merged_df.rename(columns={'priceEur': 'price_prediction'}, inplace=True)

merged_df.drop(columns=['date', 'hour', 'DateTime','renewable_ratio', 'Difference_24', 'Difference_168', 'Workday', 'Workday_168', 'Workday_24', 'forecast', 'BV Forecast', 'price_lag_24', 'price_lag_168', 'Hour_y', 'forecasted_price_eur'], inplace=True)

merged_df


Test Date  Hour_x Prediction Date  price_prediction
0     2023-04-25       0      2022-01-30             88.76
1     2023-04-25       1      2022-01-30             88.76
2     2023-04-25       2      2022-01-30             88.76
3     2023-04-25       3      2022-01-30             88.76
4     2023-04-25       4      2022-01-30             88.76
...          ...     ...             ...               ...
8803  2024-04-25      19      2023-03-12            152.11
8804  2024-04-25      20      2023-03-12             94.01
8805  2024-04-25      21      2023-03-12            129.67
8806  2024-04-25      22      2023-03-12             87.28
8807  2024-04-25      23      2023-03-12             58.35

[8808 rows x 4 columns]

In [17]:
from eptr2 import EPTR2

eptr = EPTR2(
    ssl_verify=True,
    postprocess=False,  
    get_raw_response=False
)


## solving the model

In [18]:
intraday_train = pd.read_csv('/Users/yagmurozdemir/Desktop/all_intraday_data.csv')


In [19]:
intraday_train 


contract_date contract_hour contractName    price  quantity  \
0          2021-01-14         00:00   PH21011402   289.98         2   
1          2021-01-14         00:00   PH21011402   289.99        20   
2          2021-01-14         00:00   PH21011407   269.00         7   
3          2021-01-14         00:00   PH21011404   275.00       100   
4          2021-01-14         00:00   PH21011408   279.99        20   
...               ...           ...          ...      ...       ...   
8312652    2024-04-25         23:00   PH24042602  2250.30         1   
8312653    2024-04-25         23:00   PH24042607  2251.30         8   
8312654    2024-04-25         23:00   PH24042607  2251.30         2   
8312655    2024-04-25         23:00   PH24042607  2251.30         1   
8312656    2024-04-25         23:00   PH24042607  2251.40         5   

                 id prefix        date   hour  
0         172045281     PH  2021-01-14  02:00  
1         172045519     PH  2021-01-14  02:00  
2         172046058     PH  2021-01-14  07:00  
3         172046087     PH  2021-01-14  04:00  
4         172045984     PH  2021-01-14  08:00  
...             ...    ...         ...    ...  
8312652  3686192251     PH  2024-04-26  02:00  
8312653  3686192272     PH  2024-04-26  07:00  
8312654  3686192317     PH  2024-04-26  07:00  
8312655  3686192273     PH  2024-04-26  07:00  
8312656  3686192318     PH  2024-04-26  07:00  

[8312657 rows x 9 columns]

In [20]:
import pandas as pd

def calculate_quantiles_and_lots(intraday_data, result_data):
    intraday_data['datetime'] = pd.to_datetime(intraday_data['date'] + ' ' + intraday_data['hour'])

    results = []
    for idx, row in result_data.iterrows():
        filtered_data = intraday_data[intraday_data['datetime'] == row['Prediction Date']]

        if not filtered_data.empty:
            filtered_data = filtered_data.sort_values(by='price')
            filtered_data['cumulative_quantity'] = filtered_data['quantity'].cumsum()

            total_quantity = filtered_data['cumulative_quantity'].iloc[-1]

            target_quantiles = [0.25, 0.5, 0.75]
            targets = [total_quantity * q for q in target_quantiles]
            quantile_results = []

            for quantile, target in zip(target_quantiles, targets):
                qualifying_row = filtered_data[filtered_data['cumulative_quantity'] >= target].iloc[0]
                price_at_quantile = qualifying_row['price']
                cumulative_lots_at_quantile = total_quantity - qualifying_row['cumulative_quantity']

                quantile_results.append({
                    'Test_Date': row['Test Date'],
                    'Prediction_Date': row['Prediction Date'],
                    'Hour': row['Hour_x'],
                    'Quantile': quantile,
                    'Price_Threshold': price_at_quantile,
                    'Cumulative_Lots': cumulative_lots_at_quantile
                })

            results.extend(quantile_results)

    return pd.DataFrame(results)

all_quantiles_data = calculate_quantiles_and_lots(intraday_train, merged_df)


In [21]:
all_quantiles_data

Test_Date Prediction_Date  Hour  Quantile  Price_Threshold  \
0      2023-04-25      2022-01-30     0      0.25          1379.00   
1      2023-04-25      2022-01-30     0      0.50          1380.35   
2      2023-04-25      2022-01-30     0      0.75          1384.99   
3      2023-04-25      2022-01-30     1      0.25          1379.00   
4      2023-04-25      2022-01-30     1      0.50          1380.35   
...           ...             ...   ...       ...              ...   
26347  2024-04-25      2023-03-12    22      0.50          1169.89   
26348  2024-04-25      2023-03-12    22      0.75          1170.01   
26349  2024-04-25      2023-03-12    23      0.25          1139.98   
26350  2024-04-25      2023-03-12    23      0.50          1169.89   
26351  2024-04-25      2023-03-12    23      0.75          1170.01   

       Cumulative_Lots  
0                 6815  
1                 4553  
2                 2264  
3                 6815  
4                 4553  
...                ...  
26347             3279  
26348             1267  
26349             4933  
26350             3279  
26351             1267  

[26352 rows x 6 columns]

In [22]:
production=pd.read_csv('/Users/yagmurozdemir/Desktop/AlgopolyPerformance-PerformanceReport_2024-04-25_06-16-54.csv')
start_date = "2023-04-25"
end_date = "2024-04-26"


production = production[(production['time'] >= start_date) & (production['time'] <= end_date)]
production = production[(production['eic'] == '40W000000010903W')]
production_filtered = production[['time', 'forecast']]


production_filtered['time'] = pd.to_datetime(production_filtered['time'])

production_filtered = production_filtered.sort_values(by=['time', 'forecast'], ascending=[True, False])


production_filtered = production_filtered.drop_duplicates(subset=['time'], keep='first')

production_filtered = production_filtered.rename(columns={'forecast': 'predicted_production'})

/var/folders/ff/x1vnwffx7w54w1yt78lv97gm0000gn/T/ipykernel_66388/3554123018.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  production_filtered['time'] = pd.to_datetime(production_filtered['time'])


In [23]:
production_filtered = production_filtered.drop_duplicates(subset=['time'], keep='first')

production_filtered = production_filtered.rename(columns={'forecast': 'predicted_production'})
production_filtered

time  predicted_production
454702 2023-04-25 00:00:00+00:00              5.460000
749147 2023-04-25 01:00:00+00:00              7.060000
64952  2023-04-25 02:00:00+00:00              7.720000
584674 2023-04-25 03:00:00+00:00              9.060000
108499 2023-04-25 04:00:00+00:00             14.025820
...                          ...                   ...
718571 2024-04-25 19:00:00+00:00             34.022834
34510  2024-04-25 20:00:00+00:00             26.371937
522251 2024-04-25 21:00:00+00:00             26.119594
522253 2024-04-25 22:00:00+00:00             23.361012
34520  2024-04-25 23:00:00+00:00             18.333687

[8808 rows x 2 columns]

In [24]:
merged_df


Test Date  Hour_x Prediction Date  price_prediction
0     2023-04-25       0      2022-01-30             88.76
1     2023-04-25       1      2022-01-30             88.76
2     2023-04-25       2      2022-01-30             88.76
3     2023-04-25       3      2022-01-30             88.76
4     2023-04-25       4      2022-01-30             88.76
...          ...     ...             ...               ...
8803  2024-04-25      19      2023-03-12            152.11
8804  2024-04-25      20      2023-03-12             94.01
8805  2024-04-25      21      2023-03-12            129.67
8806  2024-04-25      22      2023-03-12             87.28
8807  2024-04-25      23      2023-03-12             58.35

[8808 rows x 4 columns]

In [25]:
forecasts_df = merged_df.copy()
forecasts_df

Test Date  Hour_x Prediction Date  price_prediction
0     2023-04-25       0      2022-01-30             88.76
1     2023-04-25       1      2022-01-30             88.76
2     2023-04-25       2      2022-01-30             88.76
3     2023-04-25       3      2022-01-30             88.76
4     2023-04-25       4      2022-01-30             88.76
...          ...     ...             ...               ...
8803  2024-04-25      19      2023-03-12            152.11
8804  2024-04-25      20      2023-03-12             94.01
8805  2024-04-25      21      2023-03-12            129.67
8806  2024-04-25      22      2023-03-12             87.28
8807  2024-04-25      23      2023-03-12             58.35

[8808 rows x 4 columns]

In [26]:
forecasts_df['DateTime'] = pd.to_datetime(forecasts_df['Test Date'].astype(str) + ' ' + forecasts_df['Hour_x'].astype(str) + ':00:00+00:00')

forecasts_df.drop(columns=['Test Date', 'Hour_x'], inplace=True)

forecasts_df

Prediction Date  price_prediction                  DateTime
0         2022-01-30             88.76 2023-04-25 00:00:00+00:00
1         2022-01-30             88.76 2023-04-25 01:00:00+00:00
2         2022-01-30             88.76 2023-04-25 02:00:00+00:00
3         2022-01-30             88.76 2023-04-25 03:00:00+00:00
4         2022-01-30             88.76 2023-04-25 04:00:00+00:00
...              ...               ...                       ...
8803      2023-03-12            152.11 2024-04-25 19:00:00+00:00
8804      2023-03-12             94.01 2024-04-25 20:00:00+00:00
8805      2023-03-12            129.67 2024-04-25 21:00:00+00:00
8806      2023-03-12             87.28 2024-04-25 22:00:00+00:00
8807      2023-03-12             58.35 2024-04-25 23:00:00+00:00

[8808 rows x 3 columns]

In [27]:
forecasts_df['DateTime'] = pd.to_datetime(forecasts_df['DateTime']).dt.tz_localize(None)
production_filtered['time'] = pd.to_datetime(production_filtered['time']).dt.tz_localize(None)


production_filtered['time'] = pd.to_datetime(production_filtered['time']).dt.tz_localize(None)

merged_data = pd.merge(forecasts_df, production_filtered, left_on='DateTime', right_on='time', how='left')

merged_data.drop(columns='time', inplace=True)

In [28]:
merged_data

Prediction Date  price_prediction            DateTime  \
0         2022-01-30             88.76 2023-04-25 00:00:00   
1         2022-01-30             88.76 2023-04-25 01:00:00   
2         2022-01-30             88.76 2023-04-25 02:00:00   
3         2022-01-30             88.76 2023-04-25 03:00:00   
4         2022-01-30             88.76 2023-04-25 04:00:00   
...              ...               ...                 ...   
8803      2023-03-12            152.11 2024-04-25 19:00:00   
8804      2023-03-12             94.01 2024-04-25 20:00:00   
8805      2023-03-12            129.67 2024-04-25 21:00:00   
8806      2023-03-12             87.28 2024-04-25 22:00:00   
8807      2023-03-12             58.35 2024-04-25 23:00:00   

      predicted_production  
0                 5.460000  
1                 7.060000  
2                 7.720000  
3                 9.060000  
4                14.025820  
...                    ...  
8803             34.022834  
8804             26.371937  
8805             26.119594  
8806             23.361012  
8807             18.333687  

[8808 rows x 4 columns]

In [29]:
result_df_expanded = pd.concat([merged_data]*3, ignore_index=True).sort_values(by='DateTime')

result_df_expanded['Hour'] = result_df_expanded['DateTime'].dt.strftime('%H:%M')

In [30]:
result_df_expanded['DateTime'] = pd.to_datetime(result_df_expanded['DateTime'])

result_df_expanded

Prediction Date  price_prediction            DateTime  \
0          2022-01-30             88.76 2023-04-25 00:00:00   
17616      2022-01-30             88.76 2023-04-25 00:00:00   
8808       2022-01-30             88.76 2023-04-25 00:00:00   
1          2022-01-30             88.76 2023-04-25 01:00:00   
17617      2022-01-30             88.76 2023-04-25 01:00:00   
...               ...               ...                 ...   
8806       2023-03-12             87.28 2024-04-25 22:00:00   
17614      2023-03-12             87.28 2024-04-25 22:00:00   
17615      2023-03-12             58.35 2024-04-25 23:00:00   
8807       2023-03-12             58.35 2024-04-25 23:00:00   
26423      2023-03-12             58.35 2024-04-25 23:00:00   

       predicted_production   Hour  
0                  5.460000  00:00  
17616              5.460000  00:00  
8808               5.460000  00:00  
1                  7.060000  01:00  
17617              7.060000  01:00  
...                     ...    ...  
8806              23.361012  22:00  
17614             23.361012  22:00  
17615             18.333687  23:00  
8807              18.333687  23:00  
26423             18.333687  23:00  

[26424 rows x 5 columns]

In [31]:
result_df_expanded.to_csv('result_df_expanded.csv', index=False)
#all_quantiles_data.to_csv('all_quantiles_data.csv', index = False)

In [32]:
all_quantiles_data

Test_Date Prediction_Date  Hour  Quantile  Price_Threshold  \
0      2023-04-25      2022-01-30     0      0.25          1379.00   
1      2023-04-25      2022-01-30     0      0.50          1380.35   
2      2023-04-25      2022-01-30     0      0.75          1384.99   
3      2023-04-25      2022-01-30     1      0.25          1379.00   
4      2023-04-25      2022-01-30     1      0.50          1380.35   
...           ...             ...   ...       ...              ...   
26347  2024-04-25      2023-03-12    22      0.50          1169.89   
26348  2024-04-25      2023-03-12    22      0.75          1170.01   
26349  2024-04-25      2023-03-12    23      0.25          1139.98   
26350  2024-04-25      2023-03-12    23      0.50          1169.89   
26351  2024-04-25      2023-03-12    23      0.75          1170.01   

       Cumulative_Lots  
0                 6815  
1                 4553  
2                 2264  
3                 6815  
4                 4553  
...                ...  
26347             3279  
26348             1267  
26349             4933  
26350             3279  
26351             1267  

[26352 rows x 6 columns]

In [33]:
import pandas as pd

all_quantiles_data['Test_Date'] = pd.to_datetime(all_quantiles_data['Test_Date'])

all_quantiles_data['Prediction_Date'] = pd.to_datetime(all_quantiles_data['Prediction_Date'])


In [34]:
all_quantiles_data['Date_with_hour'] = pd.to_datetime(all_quantiles_data['Test_Date'].astype(str) + ' ' + all_quantiles_data['Hour'].astype(str) + ':00:00+00:00')
all_quantiles_data

Test_Date Prediction_Date  Hour  Quantile  Price_Threshold  \
0     2023-04-25      2022-01-30     0      0.25          1379.00   
1     2023-04-25      2022-01-30     0      0.50          1380.35   
2     2023-04-25      2022-01-30     0      0.75          1384.99   
3     2023-04-25      2022-01-30     1      0.25          1379.00   
4     2023-04-25      2022-01-30     1      0.50          1380.35   
...          ...             ...   ...       ...              ...   
26347 2024-04-25      2023-03-12    22      0.50          1169.89   
26348 2024-04-25      2023-03-12    22      0.75          1170.01   
26349 2024-04-25      2023-03-12    23      0.25          1139.98   
26350 2024-04-25      2023-03-12    23      0.50          1169.89   
26351 2024-04-25      2023-03-12    23      0.75          1170.01   

       Cumulative_Lots            Date_with_hour  
0                 6815 2023-04-25 00:00:00+00:00  
1                 4553 2023-04-25 00:00:00+00:00  
2                 2264 2023-04-25 00:00:00+00:00  
3                 6815 2023-04-25 01:00:00+00:00  
4                 4553 2023-04-25 01:00:00+00:00  
...                ...                       ...  
26347             3279 2024-04-25 22:00:00+00:00  
26348             1267 2024-04-25 22:00:00+00:00  
26349             4933 2024-04-25 23:00:00+00:00  
26350             3279 2024-04-25 23:00:00+00:00  
26351             1267 2024-04-25 23:00:00+00:00  

[26352 rows x 7 columns]

In [35]:
result_df_expanded['DateTime'] = pd.to_datetime(result_df_expanded['DateTime']).dt.tz_localize(None)
all_quantiles_data['Date_with_hour'] = pd.to_datetime(all_quantiles_data['Date_with_hour']).dt.tz_localize(None)


In [36]:
all_quantiles_data

Test_Date Prediction_Date  Hour  Quantile  Price_Threshold  \
0     2023-04-25      2022-01-30     0      0.25          1379.00   
1     2023-04-25      2022-01-30     0      0.50          1380.35   
2     2023-04-25      2022-01-30     0      0.75          1384.99   
3     2023-04-25      2022-01-30     1      0.25          1379.00   
4     2023-04-25      2022-01-30     1      0.50          1380.35   
...          ...             ...   ...       ...              ...   
26347 2024-04-25      2023-03-12    22      0.50          1169.89   
26348 2024-04-25      2023-03-12    22      0.75          1170.01   
26349 2024-04-25      2023-03-12    23      0.25          1139.98   
26350 2024-04-25      2023-03-12    23      0.50          1169.89   
26351 2024-04-25      2023-03-12    23      0.75          1170.01   

       Cumulative_Lots      Date_with_hour  
0                 6815 2023-04-25 00:00:00  
1                 4553 2023-04-25 00:00:00  
2                 2264 2023-04-25 00:00:00  
3                 6815 2023-04-25 01:00:00  
4                 4553 2023-04-25 01:00:00  
...                ...                 ...  
26347             3279 2024-04-25 22:00:00  
26348             1267 2024-04-25 22:00:00  
26349             4933 2024-04-25 23:00:00  
26350             3279 2024-04-25 23:00:00  
26351             1267 2024-04-25 23:00:00  

[26352 rows x 7 columns]

In [37]:
result_df_expanded

Prediction Date  price_prediction            DateTime  \
0          2022-01-30             88.76 2023-04-25 00:00:00   
17616      2022-01-30             88.76 2023-04-25 00:00:00   
8808       2022-01-30             88.76 2023-04-25 00:00:00   
1          2022-01-30             88.76 2023-04-25 01:00:00   
17617      2022-01-30             88.76 2023-04-25 01:00:00   
...               ...               ...                 ...   
8806       2023-03-12             87.28 2024-04-25 22:00:00   
17614      2023-03-12             87.28 2024-04-25 22:00:00   
17615      2023-03-12             58.35 2024-04-25 23:00:00   
8807       2023-03-12             58.35 2024-04-25 23:00:00   
26423      2023-03-12             58.35 2024-04-25 23:00:00   

       predicted_production   Hour  
0                  5.460000  00:00  
17616              5.460000  00:00  
8808               5.460000  00:00  
1                  7.060000  01:00  
17617              7.060000  01:00  
...                     ...    ...  
8806              23.361012  22:00  
17614             23.361012  22:00  
17615             18.333687  23:00  
8807              18.333687  23:00  
26423             18.333687  23:00  

[26424 rows x 5 columns]

In [38]:
merged_df = pd.merge(result_df_expanded, all_quantiles_data, left_on='DateTime', right_on='Date_with_hour', how='outer', indicator=True)

mismatched_rows = merged_df[merged_df['_merge'] != 'both']

print("Rows with dates that do not match in both DataFrames:")
print(mismatched_rows[['Date_with_hour', 'DateTime', '_merge']])


Rows with dates that do not match in both DataFrames:
      Date_with_hour            DateTime     _merge
69120            NaT 2024-03-10 00:00:00  left_only
69121            NaT 2024-03-10 00:00:00  left_only
69122            NaT 2024-03-10 00:00:00  left_only
69123            NaT 2024-03-10 01:00:00  left_only
69124            NaT 2024-03-10 01:00:00  left_only
...              ...                 ...        ...
69187            NaT 2024-03-10 22:00:00  left_only
69188            NaT 2024-03-10 22:00:00  left_only
69189            NaT 2024-03-10 23:00:00  left_only
69190            NaT 2024-03-10 23:00:00  left_only
69191            NaT 2024-03-10 23:00:00  left_only

[72 rows x 3 columns]


In [39]:
merged_df

Prediction Date  price_prediction            DateTime  \
0          2022-01-30             88.76 2023-04-25 00:00:00   
1          2022-01-30             88.76 2023-04-25 00:00:00   
2          2022-01-30             88.76 2023-04-25 00:00:00   
3          2022-01-30             88.76 2023-04-25 00:00:00   
4          2022-01-30             88.76 2023-04-25 00:00:00   
...               ...               ...                 ...   
79123      2023-03-12             58.35 2024-04-25 23:00:00   
79124      2023-03-12             58.35 2024-04-25 23:00:00   
79125      2023-03-12             58.35 2024-04-25 23:00:00   
79126      2023-03-12             58.35 2024-04-25 23:00:00   
79127      2023-03-12             58.35 2024-04-25 23:00:00   

       predicted_production Hour_x  Test_Date Prediction_Date  Hour_y  \
0                  5.460000  00:00 2023-04-25      2022-01-30     0.0   
1                  5.460000  00:00 2023-04-25      2022-01-30     0.0   
2                  5.460000  00:00 2023-04-25      2022-01-30     0.0   
3                  5.460000  00:00 2023-04-25      2022-01-30     0.0   
4                  5.460000  00:00 2023-04-25      2022-01-30     0.0   
...                     ...    ...        ...             ...     ...   
79123             18.333687  23:00 2024-04-25      2023-03-12    23.0   
79124             18.333687  23:00 2024-04-25      2023-03-12    23.0   
79125             18.333687  23:00 2024-04-25      2023-03-12    23.0   
79126             18.333687  23:00 2024-04-25      2023-03-12    23.0   
79127             18.333687  23:00 2024-04-25      2023-03-12    23.0   

       Quantile  Price_Threshold  Cumulative_Lots      Date_with_hour _merge  
0          0.25          1379.00           6815.0 2023-04-25 00:00:00   both  
1          0.50          1380.35           4553.0 2023-04-25 00:00:00   both  
2          0.75          1384.99           2264.0 2023-04-25 00:00:00   both  
3          0.25          1379.00           6815.0 2023-04-25 00:00:00   both  
4          0.50          1380.35           4553.0 2023-04-25 00:00:00   both  
...         ...              ...              ...                 ...    ...  
79123      0.50          1169.89           3279.0 2024-04-25 23:00:00   both  
79124      0.75          1170.01           1267.0 2024-04-25 23:00:00   both  
79125      0.25          1139.98           4933.0 2024-04-25 23:00:00   both  
79126      0.50          1169.89           3279.0 2024-04-25 23:00:00   both  
79127      0.75          1170.01           1267.0 2024-04-25 23:00:00   both  

[79128 rows x 13 columns]

In [40]:
merged_df = merged_df.drop_duplicates()
merged_df

Prediction Date  price_prediction            DateTime  \
0          2022-01-30             88.76 2023-04-25 00:00:00   
1          2022-01-30             88.76 2023-04-25 00:00:00   
2          2022-01-30             88.76 2023-04-25 00:00:00   
9          2022-01-30             88.76 2023-04-25 01:00:00   
10         2022-01-30             88.76 2023-04-25 01:00:00   
...               ...               ...                 ...   
79111      2023-03-12             87.28 2024-04-25 22:00:00   
79112      2023-03-12             87.28 2024-04-25 22:00:00   
79119      2023-03-12             58.35 2024-04-25 23:00:00   
79120      2023-03-12             58.35 2024-04-25 23:00:00   
79121      2023-03-12             58.35 2024-04-25 23:00:00   

       predicted_production Hour_x  Test_Date Prediction_Date  Hour_y  \
0                  5.460000  00:00 2023-04-25      2022-01-30     0.0   
1                  5.460000  00:00 2023-04-25      2022-01-30     0.0   
2                  5.460000  00:00 2023-04-25      2022-01-30     0.0   
9                  7.060000  01:00 2023-04-25      2022-01-30     1.0   
10                 7.060000  01:00 2023-04-25      2022-01-30     1.0   
...                     ...    ...        ...             ...     ...   
79111             23.361012  22:00 2024-04-25      2023-03-12    22.0   
79112             23.361012  22:00 2024-04-25      2023-03-12    22.0   
79119             18.333687  23:00 2024-04-25      2023-03-12    23.0   
79120             18.333687  23:00 2024-04-25      2023-03-12    23.0   
79121             18.333687  23:00 2024-04-25      2023-03-12    23.0   

       Quantile  Price_Threshold  Cumulative_Lots      Date_with_hour _merge  
0          0.25          1379.00           6815.0 2023-04-25 00:00:00   both  
1          0.50          1380.35           4553.0 2023-04-25 00:00:00   both  
2          0.75          1384.99           2264.0 2023-04-25 00:00:00   both  
9          0.25          1379.00           6815.0 2023-04-25 01:00:00   both  
10         0.50          1380.35           4553.0 2023-04-25 01:00:00   both  
...         ...              ...              ...                 ...    ...  
79111      0.50          1169.89           3279.0 2024-04-25 22:00:00   both  
79112      0.75          1170.01           1267.0 2024-04-25 22:00:00   both  
79119      0.25          1139.98           4933.0 2024-04-25 23:00:00   both  
79120      0.50          1169.89           3279.0 2024-04-25 23:00:00   both  
79121      0.75          1170.01           1267.0 2024-04-25 23:00:00   both  

[26376 rows x 13 columns]

In [41]:
#####all_quantiles_data_trimmed = all_quantiles_data.iloc[:26364]
import pandas as pd

def convert_to_dataframe(data):
    items = data['items']
    
    df = pd.DataFrame(items)
    
    df['date'] = pd.to_datetime(df['date'])
    
    return df

In [42]:
eptr = EPTR2(
    ssl_verify=True,
    postprocess=False, 
    get_raw_response=False
)

In [43]:
start_date = pd.to_datetime("2021-01-01")
end_date = pd.to_datetime("2024-04-25")
inflation = eptr.call("mcp", start_date=start_date, end_date=end_date)
inflation = convert_to_dataframe(inflation)
inflation['inflation_rate'] = inflation['price'] / inflation['priceEur']
inflation = pd.concat([inflation], ignore_index=True).sort_values(by='date')

inflation


date   hour    price  priceUsd  priceEur  \
0     2021-01-01 00:00:00+03:00  00:00   263.99     35.96     29.31   
1     2021-01-01 01:00:00+03:00  01:00   236.99     32.29     26.31   
2     2021-01-01 02:00:00+03:00  02:00   216.70     29.52     24.06   
3     2021-01-01 03:00:00+03:00  03:00   218.07     29.71     24.21   
4     2021-01-01 04:00:00+03:00  04:00   208.99     28.47     23.20   
...                         ...    ...      ...       ...       ...   
29059 2024-04-25 19:00:00+03:00  19:00  2700.00     83.08     77.99   
29060 2024-04-25 20:00:00+03:00  20:00  2700.00     83.08     77.99   
29061 2024-04-25 21:00:00+03:00  21:00  2700.00     83.08     77.99   
29062 2024-04-25 22:00:00+03:00  22:00  2700.00     83.08     77.99   
29063 2024-04-25 23:00:00+03:00  23:00  2700.00     83.08     77.99   

       inflation_rate  
0            9.006824  
1            9.007602  
2            9.006650  
3            9.007435  
4            9.008190  
...               ...  
29059       34.619823  
29060       34.619823  
29061       34.619823  
29062       34.619823  
29063       34.619823  

[29064 rows x 6 columns]

In [44]:

merged_df['Prediction_Date'] = pd.to_datetime(merged_df['Prediction_Date']).dt.tz_localize('UTC')
inflation['date'] = pd.to_datetime(inflation['date']).dt.tz_convert('UTC')

merged_df = merged_df.merge(inflation[['date', 'inflation_rate']], left_on='Prediction_Date', right_on='date', how='left')

merged_df.rename(columns={'inflation_rate': 'exchange_rate'}, inplace=True)

merged_df.drop(columns=['date'], inplace=True)

/var/folders/ff/x1vnwffx7w54w1yt78lv97gm0000gn/T/ipykernel_66388/1365466631.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  merged_df['Prediction_Date'] = pd.to_datetime(merged_df['Prediction_Date']).dt.tz_localize('UTC')


In [45]:
merged_df

Prediction Date  price_prediction            DateTime  \
0          2022-01-30             88.76 2023-04-25 00:00:00   
1          2022-01-30             88.76 2023-04-25 00:00:00   
2          2022-01-30             88.76 2023-04-25 00:00:00   
3          2022-01-30             88.76 2023-04-25 01:00:00   
4          2022-01-30             88.76 2023-04-25 01:00:00   
...               ...               ...                 ...   
26371      2023-03-12             87.28 2024-04-25 22:00:00   
26372      2023-03-12             87.28 2024-04-25 22:00:00   
26373      2023-03-12             58.35 2024-04-25 23:00:00   
26374      2023-03-12             58.35 2024-04-25 23:00:00   
26375      2023-03-12             58.35 2024-04-25 23:00:00   

       predicted_production Hour_x  Test_Date           Prediction_Date  \
0                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
1                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
2                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
3                  7.060000  01:00 2023-04-25 2022-01-30 00:00:00+00:00   
4                  7.060000  01:00 2023-04-25 2022-01-30 00:00:00+00:00   
...                     ...    ...        ...                       ...   
26371             23.361012  22:00 2024-04-25 2023-03-12 00:00:00+00:00   
26372             23.361012  22:00 2024-04-25 2023-03-12 00:00:00+00:00   
26373             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   
26374             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   
26375             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   

       Hour_y  Quantile  Price_Threshold  Cumulative_Lots      Date_with_hour  \
0         0.0      0.25          1379.00           6815.0 2023-04-25 00:00:00   
1         0.0      0.50          1380.35           4553.0 2023-04-25 00:00:00   
2         0.0      0.75          1384.99           2264.0 2023-04-25 00:00:00   
3         1.0      0.25          1379.00           6815.0 2023-04-25 01:00:00   
4         1.0      0.50          1380.35           4553.0 2023-04-25 01:00:00   
...       ...       ...              ...              ...                 ...   
26371    22.0      0.50          1169.89           3279.0 2024-04-25 22:00:00   
26372    22.0      0.75          1170.01           1267.0 2024-04-25 22:00:00   
26373    23.0      0.25          1139.98           4933.0 2024-04-25 23:00:00   
26374    23.0      0.50          1169.89           3279.0 2024-04-25 23:00:00   
26375    23.0      0.75          1170.01           1267.0 2024-04-25 23:00:00   

      _merge  exchange_rate  
0       both      15.153222  
1       both      15.153222  
2       both      15.153222  
3       both      15.153222  
4       both      15.153222  
...      ...            ...  
26371   both      20.052365  
26372   both      20.052365  
26373   both      20.052365  
26374   both      20.052365  
26375   both      20.052365  

[26376 rows x 14 columns]

In [46]:
merged_df['Price'] = merged_df['Price_Threshold'] / merged_df['exchange_rate'] 
merged_df

Prediction Date  price_prediction            DateTime  \
0          2022-01-30             88.76 2023-04-25 00:00:00   
1          2022-01-30             88.76 2023-04-25 00:00:00   
2          2022-01-30             88.76 2023-04-25 00:00:00   
3          2022-01-30             88.76 2023-04-25 01:00:00   
4          2022-01-30             88.76 2023-04-25 01:00:00   
...               ...               ...                 ...   
26371      2023-03-12             87.28 2024-04-25 22:00:00   
26372      2023-03-12             87.28 2024-04-25 22:00:00   
26373      2023-03-12             58.35 2024-04-25 23:00:00   
26374      2023-03-12             58.35 2024-04-25 23:00:00   
26375      2023-03-12             58.35 2024-04-25 23:00:00   

       predicted_production Hour_x  Test_Date           Prediction_Date  \
0                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
1                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
2                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
3                  7.060000  01:00 2023-04-25 2022-01-30 00:00:00+00:00   
4                  7.060000  01:00 2023-04-25 2022-01-30 00:00:00+00:00   
...                     ...    ...        ...                       ...   
26371             23.361012  22:00 2024-04-25 2023-03-12 00:00:00+00:00   
26372             23.361012  22:00 2024-04-25 2023-03-12 00:00:00+00:00   
26373             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   
26374             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   
26375             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   

       Hour_y  Quantile  Price_Threshold  Cumulative_Lots      Date_with_hour  \
0         0.0      0.25          1379.00           6815.0 2023-04-25 00:00:00   
1         0.0      0.50          1380.35           4553.0 2023-04-25 00:00:00   
2         0.0      0.75          1384.99           2264.0 2023-04-25 00:00:00   
3         1.0      0.25          1379.00           6815.0 2023-04-25 01:00:00   
4         1.0      0.50          1380.35           4553.0 2023-04-25 01:00:00   
...       ...       ...              ...              ...                 ...   
26371    22.0      0.50          1169.89           3279.0 2024-04-25 22:00:00   
26372    22.0      0.75          1170.01           1267.0 2024-04-25 22:00:00   
26373    23.0      0.25          1139.98           4933.0 2024-04-25 23:00:00   
26374    23.0      0.50          1169.89           3279.0 2024-04-25 23:00:00   
26375    23.0      0.75          1170.01           1267.0 2024-04-25 23:00:00   

      _merge  exchange_rate      Price  
0       both      15.153222  91.003747  
1       both      15.153222  91.092837  
2       both      15.153222  91.399043  
3       both      15.153222  91.003747  
4       both      15.153222  91.092837  
...      ...            ...        ...  
26371   both      20.052365  58.341748  
26372   both      20.052365  58.347732  
26373   both      20.052365  56.850153  
26374   both      20.052365  58.341748  
26375   both      20.052365  58.347732  

[26376 rows x 15 columns]

In [47]:
import pulp as pl
import pandas as pd
from pulp import GLPK

def setup_and_solve_trading_model(all_quantiles_data, production_wind, dayahead):
    """
    Set up and solve the linear programming problem for electricity trading optimization.

    Parameters:
    all_quantiles_data (pd.DataFrame): DataFrame containing hourly quantiles data with 'Hour', 'Quantile', 'Price', and 'Cumulative Lots'.
    production_wind (pd.DataFrame): DataFrame containing production data from wind with columns 'hour' and 'forecast'.
    dayahead (pd.DataFrame): DataFrame containing day-ahead prices with columns 'hour' and 'price'.

    Returns:
    dict: Dictionary containing the solution variables and the objective value.
    """
    if all_quantiles_data.duplicated(subset=['Hour', 'Quantile']).any():
        all_quantiles_data = all_quantiles_data.groupby(['Hour', 'Quantile']).agg({
            'Price': 'mean',
            'Cumulative_Lots': 'sum'
        }).reset_index()

    ptf_dict = all_quantiles_data.set_index(['Hour', 'Quantile']).to_dict('index')
    production_wind_dict = production_wind.set_index('hour')['forecast'].to_dict()
    dayahead_dict = dayahead.set_index('hour')['price'].to_dict()

    model = pl.LpProblem("Electricity_Trading", pl.LpMaximize)

    #time periods and quantiles
    T = dayahead['hour'].unique()  
    Q = all_quantiles_data['Quantile'].unique()

    #decision Variables
    Q1 = pl.LpVariable.dicts("Q1", T, lowBound=0)
    Q2 = pl.LpVariable.dicts("Q2", [(t, q) for t in T for q in Q], lowBound=0)

    #objective Function
    model += pl.lpSum([dayahead_dict[t] * Q1[t] for t in T if t in dayahead_dict] +
                      [ptf_dict[(t, q)]['Price'] * Q2[(t, q)] for t in T for q in Q if (t, q) in ptf_dict])

    #constraints
    for t in T:
        if t in production_wind_dict:
            model += Q1[t] + pl.lpSum([Q2[(t, q)] for q in Q if (t, q) in ptf_dict]) <= production_wind_dict[t], f"Production_{t}"

        for q in Q:
            if (t, q) in ptf_dict:
                model += Q2[(t, q)] <= ptf_dict[(t, q)]['Cumulative_Lots'], f"Demand_{t}_{q}"

    model.solve()

    results = {'Variables': {v.name: v.varValue for v in model.variables()},
               'Objective Value': pl.value(model.objective)}

    return results


In [48]:


sorted_df = merged_df.sort_values(by='DateTime')
sorted_df

Prediction Date  price_prediction            DateTime  \
0          2022-01-30             88.76 2023-04-25 00:00:00   
1          2022-01-30             88.76 2023-04-25 00:00:00   
2          2022-01-30             88.76 2023-04-25 00:00:00   
3          2022-01-30             88.76 2023-04-25 01:00:00   
4          2022-01-30             88.76 2023-04-25 01:00:00   
...               ...               ...                 ...   
26370      2023-03-12             87.28 2024-04-25 22:00:00   
26372      2023-03-12             87.28 2024-04-25 22:00:00   
26374      2023-03-12             58.35 2024-04-25 23:00:00   
26373      2023-03-12             58.35 2024-04-25 23:00:00   
26375      2023-03-12             58.35 2024-04-25 23:00:00   

       predicted_production Hour_x  Test_Date           Prediction_Date  \
0                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
1                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
2                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
3                  7.060000  01:00 2023-04-25 2022-01-30 00:00:00+00:00   
4                  7.060000  01:00 2023-04-25 2022-01-30 00:00:00+00:00   
...                     ...    ...        ...                       ...   
26370             23.361012  22:00 2024-04-25 2023-03-12 00:00:00+00:00   
26372             23.361012  22:00 2024-04-25 2023-03-12 00:00:00+00:00   
26374             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   
26373             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   
26375             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   

       Hour_y  Quantile  Price_Threshold  Cumulative_Lots      Date_with_hour  \
0         0.0      0.25          1379.00           6815.0 2023-04-25 00:00:00   
1         0.0      0.50          1380.35           4553.0 2023-04-25 00:00:00   
2         0.0      0.75          1384.99           2264.0 2023-04-25 00:00:00   
3         1.0      0.25          1379.00           6815.0 2023-04-25 01:00:00   
4         1.0      0.50          1380.35           4553.0 2023-04-25 01:00:00   
...       ...       ...              ...              ...                 ...   
26370    22.0      0.25          1139.98           4933.0 2024-04-25 22:00:00   
26372    22.0      0.75          1170.01           1267.0 2024-04-25 22:00:00   
26374    23.0      0.50          1169.89           3279.0 2024-04-25 23:00:00   
26373    23.0      0.25          1139.98           4933.0 2024-04-25 23:00:00   
26375    23.0      0.75          1170.01           1267.0 2024-04-25 23:00:00   

      _merge  exchange_rate      Price  
0       both      15.153222  91.003747  
1       both      15.153222  91.092837  
2       both      15.153222  91.399043  
3       both      15.153222  91.003747  
4       both      15.153222  91.092837  
...      ...            ...        ...  
26370   both      20.052365  56.850153  
26372   both      20.052365  58.347732  
26374   both      20.052365  58.341748  
26373   both      20.052365  56.850153  
26375   both      20.052365  58.347732  

[26376 rows x 15 columns]

In [49]:
df = sorted_df.copy()
df

Prediction Date  price_prediction            DateTime  \
0          2022-01-30             88.76 2023-04-25 00:00:00   
1          2022-01-30             88.76 2023-04-25 00:00:00   
2          2022-01-30             88.76 2023-04-25 00:00:00   
3          2022-01-30             88.76 2023-04-25 01:00:00   
4          2022-01-30             88.76 2023-04-25 01:00:00   
...               ...               ...                 ...   
26370      2023-03-12             87.28 2024-04-25 22:00:00   
26372      2023-03-12             87.28 2024-04-25 22:00:00   
26374      2023-03-12             58.35 2024-04-25 23:00:00   
26373      2023-03-12             58.35 2024-04-25 23:00:00   
26375      2023-03-12             58.35 2024-04-25 23:00:00   

       predicted_production Hour_x  Test_Date           Prediction_Date  \
0                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
1                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
2                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
3                  7.060000  01:00 2023-04-25 2022-01-30 00:00:00+00:00   
4                  7.060000  01:00 2023-04-25 2022-01-30 00:00:00+00:00   
...                     ...    ...        ...                       ...   
26370             23.361012  22:00 2024-04-25 2023-03-12 00:00:00+00:00   
26372             23.361012  22:00 2024-04-25 2023-03-12 00:00:00+00:00   
26374             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   
26373             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   
26375             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   

       Hour_y  Quantile  Price_Threshold  Cumulative_Lots      Date_with_hour  \
0         0.0      0.25          1379.00           6815.0 2023-04-25 00:00:00   
1         0.0      0.50          1380.35           4553.0 2023-04-25 00:00:00   
2         0.0      0.75          1384.99           2264.0 2023-04-25 00:00:00   
3         1.0      0.25          1379.00           6815.0 2023-04-25 01:00:00   
4         1.0      0.50          1380.35           4553.0 2023-04-25 01:00:00   
...       ...       ...              ...              ...                 ...   
26370    22.0      0.25          1139.98           4933.0 2024-04-25 22:00:00   
26372    22.0      0.75          1170.01           1267.0 2024-04-25 22:00:00   
26374    23.0      0.50          1169.89           3279.0 2024-04-25 23:00:00   
26373    23.0      0.25          1139.98           4933.0 2024-04-25 23:00:00   
26375    23.0      0.75          1170.01           1267.0 2024-04-25 23:00:00   

      _merge  exchange_rate      Price  
0       both      15.153222  91.003747  
1       both      15.153222  91.092837  
2       both      15.153222  91.399043  
3       both      15.153222  91.003747  
4       both      15.153222  91.092837  
...      ...            ...        ...  
26370   both      20.052365  56.850153  
26372   both      20.052365  58.347732  
26374   both      20.052365  58.341748  
26373   both      20.052365  56.850153  
26375   both      20.052365  58.347732  

[26376 rows x 15 columns]

In [50]:
daily_results = []
results_list = []

for date in pd.to_datetime(df['Test_Date']).dt.date.unique():
    day_data = df[pd.to_datetime(df['Test_Date']).dt.date == date]

    day_data = day_data.rename(columns={'Hour_y': 'Hour'})

    production_wind = pd.DataFrame({
        'hour': day_data['Hour'],  
        'forecast': day_data['predicted_production']  
    })

    dayahead = pd.DataFrame({
        'hour': day_data['Hour'],  
        'price': day_data['price_prediction']
    })
    
    result = setup_and_solve_trading_model(day_data[['Hour', 'Quantile', 'Price', 'Cumulative_Lots']],
                                           production_wind, dayahead)
    
    results_list.append({'date': date, 'results': result})
    daily_results.append(result)


Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/yagmurozdemir/anaconda3/lib/python3.11/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ff/x1vnwffx7w54w1yt78lv97gm0000gn/T/7dcdd274ca8046c28d462927b6b6c5c5-pulp.mps -max -timeMode elapsed -branch -printingOptions all -solution /var/folders/ff/x1vnwffx7w54w1yt78lv97gm0000gn/T/7dcdd274ca8046c28d462927b6b6c5c5-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 101 COLUMNS
At line 366 RHS
At line 463 BOUNDS
At line 464 ENDATA
Problem MODEL has 96 rows, 96 columns and 168 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Presolve 0 (-96) rows, 0 (-96) columns and 0 (-168) elements
Empty problem - 0 rows, 0 columns and 0 elements
Optimal - objective value 47941.517
After Postsolve, objective 47941.517, infeasibilities - dual 0 (0), primal 0 (0)
Optimal objective 47941.51665 - 0 iterations time 0.002, Presolve 0.00


In [51]:
daily_results

[{'Variables': {'Q1_0.0': 0.0,
   'Q1_1.0': 0.0,
   'Q1_10.0': 0.0,
   'Q1_11.0': 0.0,
   'Q1_12.0': 0.0,
   'Q1_13.0': 0.0,
   'Q1_14.0': 0.0,
   'Q1_15.0': 0.0,
   'Q1_16.0': 0.0,
   'Q1_17.0': 0.0,
   'Q1_18.0': 0.0,
   'Q1_19.0': 0.0,
   'Q1_2.0': 0.0,
   'Q1_20.0': 0.0,
   'Q1_21.0': 0.0,
   'Q1_22.0': 0.0,
   'Q1_23.0': 0.0,
   'Q1_3.0': 0.0,
   'Q1_4.0': 0.0,
   'Q1_5.0': 0.0,
   'Q1_6.0': 0.0,
   'Q1_7.0': 0.0,
   'Q1_8.0': 0.0,
   'Q1_9.0': 0.0,
   'Q2_(0.0,_0.25)': 0.0,
   'Q2_(0.0,_0.5)': 0.0,
   'Q2_(0.0,_0.75)': 5.46,
   'Q2_(1.0,_0.25)': 0.0,
   'Q2_(1.0,_0.5)': 0.0,
   'Q2_(1.0,_0.75)': 7.06,
   'Q2_(10.0,_0.25)': 0.0,
   'Q2_(10.0,_0.5)': 0.0,
   'Q2_(10.0,_0.75)': 14.88,
   'Q2_(11.0,_0.25)': 0.0,
   'Q2_(11.0,_0.5)': 0.0,
   'Q2_(11.0,_0.75)': 16.04,
   'Q2_(12.0,_0.25)': 0.0,
   'Q2_(12.0,_0.5)': 0.0,
   'Q2_(12.0,_0.75)': 18.19,
   'Q2_(13.0,_0.25)': 0.0,
   'Q2_(13.0,_0.5)': 0.0,
   'Q2_(13.0,_0.75)': 24.05,
   'Q2_(14.0,_0.25)': 0.0,
   'Q2_(14.0,_0.5)': 0.0,
   '

In [52]:
results_df = pd.DataFrame(daily_results)
results_df

Variables  Objective Value
0    {'Q1_0.0': 0.0, 'Q1_1.0': 0.0, 'Q1_10.0': 0.0,...     47941.516731
1    {'Q1_0.0': 36.164933, 'Q1_1.0': 0.0, 'Q1_10.0'...     74996.451227
2    {'Q1_0.0': 7.7, 'Q1_1.0': 3.2001944, 'Q1_10.0'...     48537.007992
3    {'Q1_0.0': 0.0, 'Q1_1.0': 0.0, 'Q1_10.0': 65.1...    303357.845663
4    {'Q1_0.0': 0.0, 'Q1_1.0': 0.0, 'Q1_10.0': 0.0,...     91191.934800
..                                                 ...              ...
362  {'Q1_0.0': 1.08, 'Q1_1.0': 1.21, 'Q1_10.0': 11...     55232.233033
363  {'Q1_0.0': 48.86, 'Q1_1.0': 48.011748, 'Q1_10....     32053.027579
364  {'Q1_0.0': 0.0, 'Q1_1.0': 0.0, 'Q1_10.0': 18.0...     91316.982381
365  {'Q1_0.0': 60.516254, 'Q1_1.0': 55.244323, 'Q1...     70896.671399
366  {'Q1_0.0': 6.8791874, 'Q1_1.0': 5.75, 'Q1_10.0...     53052.605992

[367 rows x 2 columns]

In [53]:
from datetime import datetime, timedelta

current_date = datetime.strptime('2023-04-25', '%Y-%m-%d')

structured_results = []

for result in daily_results:
    day_dict = {'Date': current_date.strftime('%Y-%m-%d')}
    day_dict.update(result['Variables'])
    day_dict['Objective Value'] = result['Objective Value']
    structured_results.append(day_dict)
    current_date += timedelta(days=1)


results_df = pd.DataFrame(structured_results)

expected_total_revenue = results_df['Objective Value'].sum()

In [54]:
results_df

Date     Q1_0.0     Q1_1.0    Q1_10.0    Q1_11.0    Q1_12.0  \
0    2023-04-25   0.000000   0.000000   0.000000   0.000000   0.000000   
1    2023-04-26  36.164933   0.000000  35.740000  36.809585   0.000000   
2    2023-04-27   7.700000   3.200194   9.736142  19.401961  33.165177   
3    2023-04-28   0.000000   0.000000  65.183483  64.742163   0.000000   
4    2023-04-29   0.000000   0.000000   0.000000   0.000000   0.000000   
..          ...        ...        ...        ...        ...        ...   
362  2024-04-21   1.080000   1.210000  11.180000  14.710000  19.560000   
363  2024-04-22  48.860000  48.011748  10.220000   8.070000   6.180000   
364  2024-04-23   0.000000   0.000000  18.079078  13.920168   0.000000   
365  2024-04-24  60.516254  55.244323  51.901532  51.796315  51.652194   
366  2024-04-25   6.879187   5.750000  23.449100  25.016439  34.365803   

       Q1_13.0    Q1_14.0    Q1_15.0    Q1_16.0  ...  Q2_(7.0,_0.5)  \
0     0.000000   0.000000   0.000000   0.000000  ...            0.0   
1     0.000000  39.687119  39.163860  42.964821  ...            0.0   
2    49.118990  55.871299  62.272400  64.894086  ...            0.0   
3    63.420525  62.071083  61.163052  61.940584  ...            0.0   
4     0.000000   0.000000   0.000000   0.000000  ...            0.0   
..         ...        ...        ...        ...  ...            ...   
362  26.240000  33.560000  42.830000  47.780000  ...            0.0   
363   4.500000   3.860000   3.660000   3.380000  ...            0.0   
364  13.360926  18.053112  31.122162  42.677646  ...            0.0   
365  44.702179  42.220000  37.210000  28.770000  ...            0.0   
366  42.465917  51.728305  52.857976  53.161239  ...            0.0   

     Q2_(7.0,_0.75)  Q2_(8.0,_0.25)  Q2_(8.0,_0.5)  Q2_(8.0,_0.75)  \
0         15.630000             0.0            0.0       13.170000   
1         33.670000             0.0            0.0       34.410000   
2          1.310000             0.0            0.0        1.550000   
3          0.000000             0.0            0.0        0.000000   
4         35.961083             0.0            0.0       39.578429   
..              ...             ...            ...             ...   
362        0.000000             0.0            0.0        0.000000   
363        0.000000             0.0            0.0        0.000000   
364       15.676816             0.0            0.0       16.867324   
365        0.000000             0.0            0.0        0.000000   
366        0.000000             0.0            0.0        0.000000   

     Q2_(9.0,_0.25)  Q2_(9.0,_0.5)  Q2_(9.0,_0.75)  Objective Value  __dummy  
0               0.0            0.0       13.540000     47941.516731      NaN  
1               0.0            0.0        0.000000     74996.451227      NaN  
2               0.0            0.0        0.000000     48537.007992      NaN  
3               0.0            0.0        0.000000    303357.845663      NaN  
4               0.0            0.0       46.756051     91191.934800      NaN  
..              ...            ...             ...              ...      ...  
362             0.0            0.0        0.000000     55232.233033      NaN  
363             0.0            0.0        0.000000     32053.027579      NaN  
364             0.0            0.0        0.000000     91316.982381      NaN  
365             0.0            0.0        0.000000     70896.671399      NaN  
366             0.0            0.0        0.000000     53052.605992      NaN  

[367 rows x 99 columns]

In [55]:
expected_total_revenue

22717605.587877512

In [56]:
results_df.to_csv('trading_optimization_results_expected_knn_model.csv', index=False)


## control

In [57]:
start_date = pd.to_datetime("2023-04-25")
end_date = pd.to_datetime("2024-04-25")
real_hourly_prices = eptr.call("mcp", start_date=start_date, end_date=end_date)
real_hourly_prices = convert_to_dataframe(real_hourly_prices)

In [58]:
real_hourly_prices = real_hourly_prices.drop(columns=['price', 'priceUsd'])
real_hourly_prices['price'] = real_hourly_prices['priceEur'] 
real_hourly_prices = real_hourly_prices.drop(columns=['priceEur'])

real_hourly_prices

date   hour   price
0    2023-04-25 00:00:00+03:00  00:00  122.57
1    2023-04-25 01:00:00+03:00  01:00  122.57
2    2023-04-25 02:00:00+03:00  02:00  105.39
3    2023-04-25 03:00:00+03:00  03:00   80.14
4    2023-04-25 04:00:00+03:00  04:00   80.14
...                        ...    ...     ...
8803 2024-04-25 19:00:00+03:00  19:00   77.99
8804 2024-04-25 20:00:00+03:00  20:00   77.99
8805 2024-04-25 21:00:00+03:00  21:00   77.99
8806 2024-04-25 22:00:00+03:00  22:00   77.99
8807 2024-04-25 23:00:00+03:00  23:00   77.99

[8808 rows x 3 columns]

In [59]:
intraday_real = pd.read_csv('/Users/yagmurozdemir/Desktop/all_intraday_data.csv')
intraday_real['date'] = pd.to_datetime(intraday_real['date'])

intraday_real = intraday_real[intraday_real['date'].between('2023-04-25', '2024-04-25')]

intraday_real

contract_date contract_hour contractName    price  quantity  \
4364172    2023-04-24         18:00   PH23042500  2522.04       150   
4364173    2023-04-24         18:00   PH23042500  2525.01       150   
4364174    2023-04-24         18:00   PH23042500  2600.00         3   
4364175    2023-04-24         18:00   PH23042500  2525.02        11   
4364176    2023-04-24         18:00   PH23042500  2525.03         5   
...               ...           ...          ...      ...       ...   
8310441    2024-04-25         21:00   PH24042523  2600.10        42   
8310442    2024-04-25         21:00   PH24042523  2600.00        24   
8310443    2024-04-25         21:00   PH24042523  2592.00        20   
8310447    2024-04-25         21:00   PH24042523  2506.10        20   
8310467    2024-04-25         21:00   PH24042523  2699.90        79   

                 id prefix       date   hour  
4364172  2036990149     PH 2023-04-25  00:00  
4364173  2036990492     PH 2023-04-25  00:00  
4364174  2036990697     PH 2023-04-25  00:00  
4364175  2036990832     PH 2023-04-25  00:00  
4364176  2036991016     PH 2023-04-25  00:00  
...             ...    ...        ...    ...  
8310441  3686190000     PH 2024-04-25  23:00  
8310442  3686190001     PH 2024-04-25  23:00  
8310443  3686190082     PH 2024-04-25  23:00  
8310447  3686190084     PH 2024-04-25  23:00  
8310467  3686190056     PH 2024-04-25  23:00  

[3942234 rows x 9 columns]

In [60]:
eptr = EPTR2(
    ssl_verify=True,
    postprocess=False,  
    get_raw_response=False
)


In [61]:
inflation = eptr.call("mcp", start_date=start_date, end_date=end_date)
inflation = convert_to_dataframe(inflation)
inflation['inflation_rate'] = inflation['price'] / inflation['priceEur']
inflation = pd.concat([inflation]*3, ignore_index=True).sort_values(by='date')


In [62]:
inflation = inflation.drop(columns=['price', 'priceUsd', 'priceUsd', 'priceEur'])

inflation

date   hour  inflation_rate
0     2023-04-25 00:00:00+03:00  00:00       21.212368
17616 2023-04-25 00:00:00+03:00  00:00       21.212368
8808  2023-04-25 00:00:00+03:00  00:00       21.212368
1     2023-04-25 01:00:00+03:00  01:00       21.212368
17617 2023-04-25 01:00:00+03:00  01:00       21.212368
...                         ...    ...             ...
8806  2024-04-25 22:00:00+03:00  22:00       34.619823
17614 2024-04-25 22:00:00+03:00  22:00       34.619823
17615 2024-04-25 23:00:00+03:00  23:00       34.619823
8807  2024-04-25 23:00:00+03:00  23:00       34.619823
26423 2024-04-25 23:00:00+03:00  23:00       34.619823

[26424 rows x 3 columns]

In [63]:
import pandas as pd

intraday_real['date'] = pd.to_datetime(intraday_real['date'])

intraday_real['hour'] = intraday_real['hour'].astype(str)
intraday_real['datetime'] = pd.to_datetime(intraday_real['date'].dt.date.astype(str) + ' ' + intraday_real['hour'])

inflation['date'] = pd.to_datetime(inflation['date']) 
inflation['hour'] = inflation['hour'].astype(str)
inflation['datetime'] = pd.to_datetime(inflation['date'].dt.date.astype(str) + ' ' + inflation['hour'])

merged_data = pd.merge(intraday_real, inflation, on='datetime', how='left')

merged_data['adjusted_price'] = merged_data['price'] / merged_data['inflation_rate']


merged_data


contract_date contract_hour contractName    price  quantity  \
0           2023-04-24         18:00   PH23042500  2522.04       150   
1           2023-04-24         18:00   PH23042500  2522.04       150   
2           2023-04-24         18:00   PH23042500  2522.04       150   
3           2023-04-24         18:00   PH23042500  2525.01       150   
4           2023-04-24         18:00   PH23042500  2525.01       150   
...                ...           ...          ...      ...       ...   
11826697    2024-04-25         21:00   PH24042523  2506.10        20   
11826698    2024-04-25         21:00   PH24042523  2506.10        20   
11826699    2024-04-25         21:00   PH24042523  2699.90        79   
11826700    2024-04-25         21:00   PH24042523  2699.90        79   
11826701    2024-04-25         21:00   PH24042523  2699.90        79   

                  id prefix     date_x hour_x            datetime  \
0         2036990149     PH 2023-04-25  00:00 2023-04-25 00:00:00   
1         2036990149     PH 2023-04-25  00:00 2023-04-25 00:00:00   
2         2036990149     PH 2023-04-25  00:00 2023-04-25 00:00:00   
3         2036990492     PH 2023-04-25  00:00 2023-04-25 00:00:00   
4         2036990492     PH 2023-04-25  00:00 2023-04-25 00:00:00   
...              ...    ...        ...    ...                 ...   
11826697  3686190084     PH 2024-04-25  23:00 2024-04-25 23:00:00   
11826698  3686190084     PH 2024-04-25  23:00 2024-04-25 23:00:00   
11826699  3686190056     PH 2024-04-25  23:00 2024-04-25 23:00:00   
11826700  3686190056     PH 2024-04-25  23:00 2024-04-25 23:00:00   
11826701  3686190056     PH 2024-04-25  23:00 2024-04-25 23:00:00   

                            date_y hour_y  inflation_rate  adjusted_price  
0        2023-04-25 00:00:00+03:00  00:00       21.212368      118.894786  
1        2023-04-25 00:00:00+03:00  00:00       21.212368      118.894786  
2        2023-04-25 00:00:00+03:00  00:00       21.212368      118.894786  
3        2023-04-25 00:00:00+03:00  00:00       21.212368      119.034798  
4        2023-04-25 00:00:00+03:00  00:00       21.212368      119.034798  
...                            ...    ...             ...             ...  
11826697 2024-04-25 23:00:00+03:00  23:00       34.619823       72.389163  
11826698 2024-04-25 23:00:00+03:00  23:00       34.619823       72.389163  
11826699 2024-04-25 23:00:00+03:00  23:00       34.619823       77.987111  
11826700 2024-04-25 23:00:00+03:00  23:00       34.619823       77.987111  
11826701 2024-04-25 23:00:00+03:00  23:00       34.619823       77.987111  

[11826702 rows x 14 columns]

In [64]:
df

Prediction Date  price_prediction            DateTime  \
0          2022-01-30             88.76 2023-04-25 00:00:00   
1          2022-01-30             88.76 2023-04-25 00:00:00   
2          2022-01-30             88.76 2023-04-25 00:00:00   
3          2022-01-30             88.76 2023-04-25 01:00:00   
4          2022-01-30             88.76 2023-04-25 01:00:00   
...               ...               ...                 ...   
26370      2023-03-12             87.28 2024-04-25 22:00:00   
26372      2023-03-12             87.28 2024-04-25 22:00:00   
26374      2023-03-12             58.35 2024-04-25 23:00:00   
26373      2023-03-12             58.35 2024-04-25 23:00:00   
26375      2023-03-12             58.35 2024-04-25 23:00:00   

       predicted_production Hour_x  Test_Date           Prediction_Date  \
0                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
1                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
2                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
3                  7.060000  01:00 2023-04-25 2022-01-30 00:00:00+00:00   
4                  7.060000  01:00 2023-04-25 2022-01-30 00:00:00+00:00   
...                     ...    ...        ...                       ...   
26370             23.361012  22:00 2024-04-25 2023-03-12 00:00:00+00:00   
26372             23.361012  22:00 2024-04-25 2023-03-12 00:00:00+00:00   
26374             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   
26373             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   
26375             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   

       Hour_y  Quantile  Price_Threshold  Cumulative_Lots      Date_with_hour  \
0         0.0      0.25          1379.00           6815.0 2023-04-25 00:00:00   
1         0.0      0.50          1380.35           4553.0 2023-04-25 00:00:00   
2         0.0      0.75          1384.99           2264.0 2023-04-25 00:00:00   
3         1.0      0.25          1379.00           6815.0 2023-04-25 01:00:00   
4         1.0      0.50          1380.35           4553.0 2023-04-25 01:00:00   
...       ...       ...              ...              ...                 ...   
26370    22.0      0.25          1139.98           4933.0 2024-04-25 22:00:00   
26372    22.0      0.75          1170.01           1267.0 2024-04-25 22:00:00   
26374    23.0      0.50          1169.89           3279.0 2024-04-25 23:00:00   
26373    23.0      0.25          1139.98           4933.0 2024-04-25 23:00:00   
26375    23.0      0.75          1170.01           1267.0 2024-04-25 23:00:00   

      _merge  exchange_rate      Price  
0       both      15.153222  91.003747  
1       both      15.153222  91.092837  
2       both      15.153222  91.399043  
3       both      15.153222  91.003747  
4       both      15.153222  91.092837  
...      ...            ...        ...  
26370   both      20.052365  56.850153  
26372   both      20.052365  58.347732  
26374   both      20.052365  58.341748  
26373   both      20.052365  56.850153  
26375   both      20.052365  58.347732  

[26376 rows x 15 columns]

In [67]:
import pandas as pd


def adjust_cumulative_lots(merged_df, results_df):
    for test_date in results_df['Test_Date'].unique():
        filtered_merged = merged_df[merged_df['date_x'] == test_date]

        if filtered_merged.empty:
            continue

        relevant_rows = results_df[results_df['Test_Date'] == test_date]

        if relevant_rows.empty:
            continue

        merged = pd.merge(filtered_merged, relevant_rows, left_on=['datetime', 'hour_x'], right_on=['DateTime', 'Hour_x'], suffixes=('_merged', '_results'))

        higher_prices = merged[merged['adjusted_price'] > merged['Price']]


        if not higher_prices.empty:
            total_quantities = higher_prices.groupby(higher_prices.index).agg({'quantity': 'sum'}).rename(columns={'quantity': 'total_quantity'})

            relevant_rows = relevant_rows.join(total_quantities, how='left')
            #relevant_rows['total_quantity'].fillna(0, inplace=True)

            relevant_rows['Cumulative_Lots'] = relevant_rows.apply(
                lambda x: min(x['total_quantity'], x['Cumulative_Lots']),
                axis=1
            )

    return results_df
corrected_results = adjust_cumulative_lots(merged_data, df)


In [68]:
corrected_results

Prediction Date  price_prediction            DateTime  \
0          2022-01-30             88.76 2023-04-25 00:00:00   
1          2022-01-30             88.76 2023-04-25 00:00:00   
2          2022-01-30             88.76 2023-04-25 00:00:00   
3          2022-01-30             88.76 2023-04-25 01:00:00   
4          2022-01-30             88.76 2023-04-25 01:00:00   
...               ...               ...                 ...   
26370      2023-03-12             87.28 2024-04-25 22:00:00   
26372      2023-03-12             87.28 2024-04-25 22:00:00   
26374      2023-03-12             58.35 2024-04-25 23:00:00   
26373      2023-03-12             58.35 2024-04-25 23:00:00   
26375      2023-03-12             58.35 2024-04-25 23:00:00   

       predicted_production Hour_x  Test_Date           Prediction_Date  \
0                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
1                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
2                  5.460000  00:00 2023-04-25 2022-01-30 00:00:00+00:00   
3                  7.060000  01:00 2023-04-25 2022-01-30 00:00:00+00:00   
4                  7.060000  01:00 2023-04-25 2022-01-30 00:00:00+00:00   
...                     ...    ...        ...                       ...   
26370             23.361012  22:00 2024-04-25 2023-03-12 00:00:00+00:00   
26372             23.361012  22:00 2024-04-25 2023-03-12 00:00:00+00:00   
26374             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   
26373             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   
26375             18.333687  23:00 2024-04-25 2023-03-12 00:00:00+00:00   

       Hour_y  Quantile  Price_Threshold  Cumulative_Lots      Date_with_hour  \
0         0.0      0.25          1379.00           6815.0 2023-04-25 00:00:00   
1         0.0      0.50          1380.35           4553.0 2023-04-25 00:00:00   
2         0.0      0.75          1384.99           2264.0 2023-04-25 00:00:00   
3         1.0      0.25          1379.00           6815.0 2023-04-25 01:00:00   
4         1.0      0.50          1380.35           4553.0 2023-04-25 01:00:00   
...       ...       ...              ...              ...                 ...   
26370    22.0      0.25          1139.98           4933.0 2024-04-25 22:00:00   
26372    22.0      0.75          1170.01           1267.0 2024-04-25 22:00:00   
26374    23.0      0.50          1169.89           3279.0 2024-04-25 23:00:00   
26373    23.0      0.25          1139.98           4933.0 2024-04-25 23:00:00   
26375    23.0      0.75          1170.01           1267.0 2024-04-25 23:00:00   

      _merge  exchange_rate      Price  
0       both      15.153222  91.003747  
1       both      15.153222  91.092837  
2       both      15.153222  91.399043  
3       both      15.153222  91.003747  
4       both      15.153222  91.092837  
...      ...            ...        ...  
26370   both      20.052365  56.850153  
26372   both      20.052365  58.347732  
26374   both      20.052365  58.341748  
26373   both      20.052365  56.850153  
26375   both      20.052365  58.347732  

[26376 rows x 15 columns]

In [70]:
real_hourly_prices

price
date                hour         
2023-04-25 00:00:00 00:00  122.57
2023-04-25 01:00:00 01:00  122.57
2023-04-25 02:00:00 02:00  105.39
2023-04-25 03:00:00 03:00   80.14
2023-04-25 04:00:00 04:00   80.14
...                           ...
2024-04-25 19:00:00 19:00   77.99
2024-04-25 20:00:00 20:00   77.99
2024-04-25 21:00:00 21:00   77.99
2024-04-25 22:00:00 22:00   77.99
2024-04-25 23:00:00 23:00   77.99

[8808 rows x 1 columns]

In [72]:
results_df

Date     Q1_0.0     Q1_1.0    Q1_10.0    Q1_11.0    Q1_12.0  \
0    2023-04-25   0.000000   0.000000   0.000000   0.000000   0.000000   
1    2023-04-26  36.164933   0.000000  35.740000  36.809585   0.000000   
2    2023-04-27   7.700000   3.200194   9.736142  19.401961  33.165177   
3    2023-04-28   0.000000   0.000000  65.183483  64.742163   0.000000   
4    2023-04-29   0.000000   0.000000   0.000000   0.000000   0.000000   
..          ...        ...        ...        ...        ...        ...   
362  2024-04-21   1.080000   1.210000  11.180000  14.710000  19.560000   
363  2024-04-22  48.860000  48.011748  10.220000   8.070000   6.180000   
364  2024-04-23   0.000000   0.000000  18.079078  13.920168   0.000000   
365  2024-04-24  60.516254  55.244323  51.901532  51.796315  51.652194   
366  2024-04-25   6.879187   5.750000  23.449100  25.016439  34.365803   

       Q1_13.0    Q1_14.0    Q1_15.0    Q1_16.0  ...  Q2_(7.0,_0.5)  \
0     0.000000   0.000000   0.000000   0.000000  ...            0.0   
1     0.000000  39.687119  39.163860  42.964821  ...            0.0   
2    49.118990  55.871299  62.272400  64.894086  ...            0.0   
3    63.420525  62.071083  61.163052  61.940584  ...            0.0   
4     0.000000   0.000000   0.000000   0.000000  ...            0.0   
..         ...        ...        ...        ...  ...            ...   
362  26.240000  33.560000  42.830000  47.780000  ...            0.0   
363   4.500000   3.860000   3.660000   3.380000  ...            0.0   
364  13.360926  18.053112  31.122162  42.677646  ...            0.0   
365  44.702179  42.220000  37.210000  28.770000  ...            0.0   
366  42.465917  51.728305  52.857976  53.161239  ...            0.0   

     Q2_(7.0,_0.75)  Q2_(8.0,_0.25)  Q2_(8.0,_0.5)  Q2_(8.0,_0.75)  \
0         15.630000             0.0            0.0       13.170000   
1         33.670000             0.0            0.0       34.410000   
2          1.310000             0.0            0.0        1.550000   
3          0.000000             0.0            0.0        0.000000   
4         35.961083             0.0            0.0       39.578429   
..              ...             ...            ...             ...   
362        0.000000             0.0            0.0        0.000000   
363        0.000000             0.0            0.0        0.000000   
364       15.676816             0.0            0.0       16.867324   
365        0.000000             0.0            0.0        0.000000   
366        0.000000             0.0            0.0        0.000000   

     Q2_(9.0,_0.25)  Q2_(9.0,_0.5)  Q2_(9.0,_0.75)  Objective Value  __dummy  
0               0.0            0.0       13.540000     47941.516731      NaN  
1               0.0            0.0        0.000000     74996.451227      NaN  
2               0.0            0.0        0.000000     48537.007992      NaN  
3               0.0            0.0        0.000000    303357.845663      NaN  
4               0.0            0.0       46.756051     91191.934800      NaN  
..              ...            ...             ...              ...      ...  
362             0.0            0.0        0.000000     55232.233033      NaN  
363             0.0            0.0        0.000000     32053.027579      NaN  
364             0.0            0.0        0.000000     91316.982381      NaN  
365             0.0            0.0        0.000000     70896.671399      NaN  
366             0.0            0.0        0.000000     53052.605992      NaN  

[367 rows x 99 columns]

In [73]:
import pandas as pd
import numpy as np



daily_revenues = []

for index, row in results_df.iterrows():
    day = pd.to_datetime(row['Date'])
    revenue_q1 = 0
    revenue_q2 = 0

    for i in range(24): 
        hour_key = f"{i:02}:00"
        q1_key = f"Q1_{i}.0"  
        if (day, hour_key) in real_hourly_prices.index:
            revenue_q1 += row[q1_key] * real_hourly_prices.loc[(day, hour_key), 'price']

    for i in range(24):
        hour_key = f"{i:02}:00"
        for quant in [0.25, 0.5, 0.75]:
            q2_key = f"Q2_({i}.0,_{quant})"  
            if (day, hour_key, quant) in corrected_results.set_index(['Prediction Date', 'Hour_x', 'Quantile']).index:
                price = corrected_results.loc[(day, hour_key, quant), 'Price']
                cum_lots = corrected_results.loc[(day, hour_key, quant), 'Cumulative_Lots']
                if cum_lots > row[q2_key]:
                    revenue_q2 += row[q2_key] * price
                else:
                    revenue_q2 += 0

    daily_revenues.append(revenue_q1 + revenue_q2)

daily_revenue_df = pd.DataFrame(daily_revenues, columns=['Daily Revenue'])


/var/folders/ff/x1vnwffx7w54w1yt78lv97gm0000gn/T/ipykernel_66388/165678288.py:26: PerformanceWarning: indexing past lexsort depth may impact performance.
  if (day, hour_key, quant) in corrected_results.set_index(['Prediction Date', 'Hour_x', 'Quantile']).index:
/var/folders/ff/x1vnwffx7w54w1yt78lv97gm0000gn/T/ipykernel_66388/165678288.py:26: PerformanceWarning: indexing past lexsort depth may impact performance.
  if (day, hour_key, quant) in corrected_results.set_index(['Prediction Date', 'Hour_x', 'Quantile']).index:
/var/folders/ff/x1vnwffx7w54w1yt78lv97gm0000gn/T/ipykernel_66388/165678288.py:26: PerformanceWarning: indexing past lexsort depth may impact performance.
  if (day, hour_key, quant) in corrected_results.set_index(['Prediction Date', 'Hour_x', 'Quantile']).index:
/var/folders/ff/x1vnwffx7w54w1yt78lv97gm0000gn/T/ipykernel_66388/165678288.py:26: PerformanceWarning: indexing past lexsort depth may impact performance.
  if (day, hour_key, quant) in corrected_results.set_inde

In [74]:
daily_revenue_df

Daily Revenue
0         0.000000
1      2881.983511
2       935.704000
3         0.000000
4         0.000000
..             ...
362      74.854800
363    3104.564400
364       0.000000
365    4719.662649
366     536.507825

[367 rows x 1 columns]

In [75]:
print("Total Revenue:", daily_revenue_df['Daily Revenue'].sum())


Total Revenue: 407696.53989613324


In [76]:
407696.53989613324*34.97

14257148.00016778